<a href="https://colab.research.google.com/github/ratmcu/wiki_ner/blob/master/dataset_results.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

##Loading the final dataset


In [1]:
#experiment_code
import tarfile
!pip install wget
import os
import wget
wget.download('https://archive.org/download/wikiner_dataset_csv.tar/wikiner_dataset_txt.tar.gz')
tar = tarfile.open('wikiner_dataset_txt.tar.gz', mode='r')
tar.extractall('./dataset_txt')
tar.close()
wget.download('https://archive.org/download/auto_manual_annots.tar/auto_manual_annots.tar.gz')
tar =  tarfile.open('./auto_manual_annots.tar.gz', mode='r')
tar.extractall('./auto_manual_annots')
tar.close()
import numpy as np
import torch
import pandas as pd
from torch.utils import data
!pip install pytorch-pretrained-bert
from pytorch_pretrained_bert import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-cased', do_lower_case=False)

  Created wheel for wget: filename=wget-3.2-cp36-none-any.whl size=9682 sha256=bbccb364899ce00c73c3ebfccb1dc08eef6db428f3944cebd97ce3c7b39c43da
  Stored in directory: /root/.cache/pip/wheels/40/15/30/7d8f7cea2902b4db79e3fea550d7d7b85ecb27ef992b618f3f
Successfully built wget


KeyboardInterrupt: ignored

## model

In [0]:
#experiment_code
import torch
# import torch.nn as nn
import torch.optim as optim
# from torch.utils import data
# from model import Net
# from data_load import NerDataset, pad, VOCAB, tokenizer, tag2idx, idx2tag
import os
import numpy as np
import argparse
from torchvision import datasets, transforms

# import numpy as np
# import torch
import pandas as pd
from torch.utils import data
!pip install pytorch-pretrained-bert
from pytorch_pretrained_bert import BertTokenizer
# import traceback
tokenizer = BertTokenizer.from_pretrained('bert-base-cased', do_lower_case=False)
# VOCAB = ('<PAD>', 'O', 'I-LOC', 'B-PER', 'I-PER', 'I-ORG', 'I-MISC', 'B-MISC', 'B-LOC', 'B-ORG')
from pytorch_pretrained_bert import BertModel
import pytorch_pretrained_bert


     |████████████████████████████████| 133kB 9.2MB/s 


100%|██████████| 213450/213450 [00:00<00:00, 826449.92B/s]


In [0]:
#experiment_code
import torch
import torch.nn as nn
from pytorch_pretrained_bert import BertModel

class Net(nn.Module):
    def __init__(self, top_rnns=False, vocab_size=None, device='cpu', finetuning=False):
        super().__init__()
        self.bert = BertModel.from_pretrained('bert-base-cased')

        self.top_rnns=top_rnns
        if top_rnns:
            self.rnn = nn.LSTM(bidirectional=True, num_layers=2, input_size=768, hidden_size=768//2, batch_first=True)
        self.fc = nn.Linear(768, vocab_size)

        self.device = device
        self.finetuning = finetuning

    def forward(self, x, y, ):
        '''
        x: (N, T). int64
        y: (N, T). int64
        Returns
        enc: (N, T, VOCAB)
        '''
        x = x.to(self.device)
        y = y.to(self.device)

        if self.training and self.finetuning:
            # print("->bert.train()")
            self.bert.train()
            encoded_layers, _ = self.bert(x)
            enc = encoded_layers[-1]
        else:
            self.bert.eval()
            with torch.no_grad():
                encoded_layers, _ = self.bert(x)
                enc = encoded_layers[-1]

        if self.top_rnns:
            enc, _ = self.rnn(enc)
        logits = self.fc(enc)
        y_hat = logits.argmax(-1)
        return logits, y, y_hat

 ## Data Loader

In [0]:
'''
An entry or sent looks like ...
SOCCER NN B-NP O
- : O O
JAPAN NNP B-NP B-LOC
GET VB B-VP O
LUCKY NNP B-NP O
WIN NNP I-NP O
, , O O
CHINA NNP B-NP B-PER
IN IN B-PP O
SURPRISE DT B-NP O
DEFEAT NN I-NP O
. . O O
Each mini-batch returns the followings:
words: list of input sents. ["The 26-year-old ...", ...]
x: encoded input sents. [N, T]. int64.
is_heads: list of head markers. [[1, 1, 0, ...], [...]]
tags: list of tags.['O O B-MISC ...', '...']
y: encoded tags. [N, T]. int64
seqlens: list of seqlens. [45, 49, 10, 50, ...]
'''
# # VOCAB = ('<PAD>', 'O', 'I-LOC', 'B-PER', 'I-PER', 'I-ORG', 'I-MISC', 'B-MISC', 'B-LOC', 'B-ORG')

tags = ['BD', 'BP', 'PR', 'SP', 'CH', 'ED']
VOCAB_list = ['<PAD>', 'O',]
for tag in tags:
    VOCAB_list.append('I-'+tag)
    VOCAB_list.append('B-'+tag)
VOCAB = tuple(VOCAB_list)
tag2idx = {tag: idx for idx, tag in enumerate(VOCAB)}
idx2tag = {idx: tag for idx, tag in enumerate(VOCAB)}

class NerDataset(data.Dataset):
    def __init__(self, fpath):
        """
        fpath: [train|valid|test].txt
        """
        entries = open(fpath, 'r').read().strip().split("\n\n")
        sents, tags_li = [], [] # list of lists
        for entry in entries:
#             print(entry)
            lines = entry.splitlines()
            words = [line.split()[0] for line in entry.splitlines() if len(line.split()) > 1]
#             try:
#                 words = [line.split()[0] for line in entry.splitlines()]
# #                 words = [line.split()[0] for line in entry.splitlines() if len(line.split())== 1 and line.split()[0] == 'O']
#             except Exception as e:
#                 print(traceback.format_exc())
#                 print('splitting failed: ', [(ord(char), char) for char in entry])
#                 continue
            tags = ([line.split()[-1] for line in entry.splitlines() if len(line.split()) > 1])
            if not (len(tags) != 0 and tags.count(tags[0]) == len(tags)):
                sents.append(["[CLS]"] + words + ["[SEP]"])
                tags_li.append(["<PAD>"] + tags + ["<PAD>"])
        self.sents, self.tags_li = sents, tags_li

    def __len__(self):
        return len(self.sents)

    def __getitem__(self, idx):
        words, tags = self.sents[idx], self.tags_li[idx] # words, tags: string list

        # We give credits only to the first piece.
        x, y = [], [] # list of ids
        is_heads = [] # list. 1: the token is the first piece of a word
        for w, t in zip(words, tags):
            if ord(w[0]) in [65533, 8206, 150, 61656, 128, 157] : #bad tokens that caused miss matches in the token and is_head legths
                continue 
            tokens = tokenizer.tokenize(w) if w not in ("[CLS]", "[SEP]") else [w]
            xx = tokenizer.convert_tokens_to_ids(tokens)

            is_head = [1] + [0]*(len(tokens) - 1)

            t = [t] + ["<PAD>"] * (len(tokens) - 1)  # <PAD>: no decision
            yy = [tag2idx[each] for each in t]  # (T,)

            x.extend(xx)
            is_heads.extend(is_head)
            y.extend(yy)
        try:
          assert len(x)==len(y)==len(is_heads), f"len(x)={len(x)}, len(y)={len(y)}, len(is_heads)={len(is_heads)}"
        except AssertionError:
          print(tags)
          for tag in words:
              for c in tag:
                  print(c, ord(c))
          print(words)
          print(x)
          print(y)
          print(is_heads)
          raise BaseException(f"len(x)={len(x)}, len(y)={len(y)}, len(is_heads)={len(is_heads)}")
        # seqlen
        seqlen = len(y)

        # to string
        words = " ".join(words)
        tags = " ".join(tags)
        return words, x, is_heads, tags, y, seqlen
    
    def append(self, other):
        self.sents.extend(other.sents)
        self.tags_li.extend(other.tags_li)

def pad(batch):
    '''Pads to 50'''
    f = lambda x: [sample[x] for sample in batch]
    g = lambda x, seqlen: [sample[x] + [" #!#!",[0],[0]," <PAD>"][x] * (seqlen - len(sample[x])) if len(sample[x]) < seqlen else sample[x][:seqlen] for sample in batch]  
    seqlens = f(-1)
    maxlen = min(50, np.array(seqlens).max())
    # print(type(batch[0][3]))
    # words = g(0, maxlen)
    words = f(0)
    # print(type(words))
    is_heads = g(2, maxlen)
    # print(type(is_heads))
    tags = [sample[3] for sample in batch] #g(3, maxlen)
    # print(type(tags))
    # maxlen = np.array(seqlens).max()
    # g = lambda x, seqlen: [sample[x] + [0] * (seqlen - len(sample[x])) for sample in batch] # 0: <pad>
    g = lambda x, seqlen: [ sample[x] + [0] * (seqlen - len(sample[x])) if len(sample[x]) < seqlen else sample[x][:seqlen] for sample in batch]  # 0: <pad>

    x = g(1, maxlen)
    y = g(-2, maxlen)

    f = torch.LongTensor
    # print(maxlen)
    # print(len(tags))
    # print(tags)
    return words, f(x), is_heads, tags, f(y), [maxlen for sample in batch]

def pad_max(batch):
    '''Pads to the longest sample'''
    f = lambda x: [sample[x] for sample in batch]
    words = f(0)
    is_heads = f(2)
    tags = f(3)
    seqlens = f(-1)
    maxlen = np.array(seqlens).max()

    f = lambda x, seqlen: [sample[x] + [0] * (seqlen - len(sample[x])) for sample in batch] # 0: <pad>
    x = f(1, maxlen)
    y = f(-2, maxlen)
    f = torch.LongTensor
    return words, f(x), is_heads, tags, f(y), seqlens

def pad_fed(batch):
    '''Pads always to 50 since there will be a fixed size in the embedding layer'''
    f = lambda x: [sample[x] for sample in batch]
    g = lambda x, seqlen: [sample[x] + [" #!#!",[0],[0]," <PAD>"][x] * (seqlen - len(sample[x])) if len(sample[x]) < seqlen else sample[x][:seqlen] for sample in batch]  
    seqlens = f(-1)
    # maxlen = min(50, np.array(seqlens).max())
    maxlen = 50
    words = f(0)
    is_heads = g(2, maxlen)
    tags = [sample[3] for sample in batch] 
    g = lambda x, seqlen: [ sample[x] + [0] * (seqlen - len(sample[x])) if len(sample[x]) < seqlen else sample[x][:seqlen] for sample in batch]  # 0: <pad>

    x = g(1, maxlen)
    y = g(-2, maxlen)

    f = torch.LongTensor
    return words, f(x), is_heads, tags, f(y), [maxlen for sample in batch]

def eval(model, iterator, f):
    model.eval()

    Words, Is_heads, Tags, Y, Y_hat = [], [], [], [], []
    with torch.no_grad():
        for i, batch in enumerate(iterator):
            words, x, is_heads, tags, y, seqlens = batch

            _, _, y_hat = model(x, y)  # y_hat: (N, T)

            Words.extend(words)
            Is_heads.extend(is_heads)
            Tags.extend(tags)
            Y.extend(y.numpy().tolist())
            Y_hat.extend(y_hat.cpu().numpy().tolist())

    ## gets results and save
    with open("temp", 'w') as fout:
        for words, is_heads, tags, y_hat in zip(Words, Is_heads, Tags, Y_hat):
            # print(f"len y_hat: {len(y_hat)} is_head {len(is_heads)} \n")
            y_hat = [hat for head, hat in zip(is_heads, y_hat) if head == 1]
            preds = [idx2tag[hat] for hat in y_hat]
            # assert len(preds)==len(words.split())==len(tags.split())
            # assert len(words.split())==len(tags.split())
            # print(preds, words, tags.split()[:len(preds)])
            words = [word for word in words.split()]
            # tokens = [tokenizer.tokenize(w) if w not in ("[CLS]", "[SEP]") else [w] for w in words.split()] 
            # print(preds, words, tags.split()[:len(preds)])
            tags = tags.split()[:len(preds)]
            # print(len(preds), len(words), len(tags))
            # assert len(preds)==len(words),  f"len(peds)={len(preds)}, len(words)={len(words)}, len(is_heads)={len(is_heads)}"
            for w, t, p in zip(words[1:-1], tags[1:-1], preds[1:-1]):
                fout.write(f"{w} {t} {p}\n")
            fout.write("\n")

    ## calc metric
    y_true =  np.array([tag2idx[line.split()[1]] for line in open("temp", 'r').read().splitlines() if len(line) > 0]) #original tags
    y_pred =  np.array([tag2idx[line.split()[2]] for line in open("temp", 'r').read().splitlines() if len(line) > 0]) #predicted tags

    num_proposed = len(y_pred[y_pred>1])
    num_correct = (np.logical_and(y_true==y_pred, y_true>1)).astype(np.int).sum()
    num_gold = len(y_true[y_true>1])

    print(f"num_proposed:{num_proposed}")
    print(f"num_correct:{num_correct}")
    print(f"num_gold:{num_gold}")
    
    try:
        precision = num_correct / num_proposed
    except ZeroDivisionError:
        precision = 1.0

    try:
        recall = num_correct / num_gold
    except ZeroDivisionError:
        recall = 1.0

    try:
        f1 = 2*precision*recall / (precision + recall)
    except ZeroDivisionError:
        if precision*recall==0:
            f1=1.0
        else:
            f1=0

    final = f + ".P%.2f_R%.2f_F%.2f" %(precision, recall, f1)
    with open(final, 'w') as fout:
        result = open("temp", "r").read()
        fout.write(f"{result}\n")
        fout.write(f"precision={precision}\n")
        fout.write(f"recall={recall}\n")
        fout.write(f"f1={f1}\n")

    os.remove("temp")
    print("precision=%.2f"%precision)
    print("recall=%.2f"%recall)
    print("f1=%.2f"%f1)
    return precision, recall, f1

In [0]:
# import os
paths_annot = sorted([os.path.join(f[0], name) for f in os.walk('./dataset_txt') 
                if len(f[2])!=0 for name in f[2] if os.path.splitext(name)[-1] == '.txt' and name.split('_')[0]=='annot'],
               key=lambda path: int(path.split('_')[-1].split('.')[0]))
training_files = [path for path in paths_annot if 'training' in path.split('/')]
eval_files = [path for path in paths_annot if 'eval' in path.split('/')]
test_files = [path for path in paths_annot if 'test' in path.split('/')]

In [0]:
from torch.utils import data
train_dataset = NerDataset(training_files[0])
_ = [train_dataset.append(NerDataset(train_file)) for train_file in training_files[1:]]

eval_dataset = NerDataset(eval_files[0])
_ = [eval_dataset.append(NerDataset(eval_file)) for eval_file in eval_files[1:]]

test_dataset = NerDataset(test_files[0])
_ = [test_dataset.append(NerDataset(test_file)) for test_file in test_files[1:]]

eval_iter = data.DataLoader(dataset=eval_dataset,
                              batch_size=1,
                              shuffle=True,
                              num_workers=16,
                              collate_fn=pad)

test_iter = data.DataLoader(dataset=test_dataset,
                              batch_size=1,
                              shuffle=True,
                              num_workers=16,
                              collate_fn=pad)

train_iter = data.DataLoader(dataset=train_dataset,
                              batch_size=1,
                              shuffle=True,
                              num_workers=16,
                              collate_fn=pad)
test_iter_128 = data.DataLoader(dataset=test_dataset,
                              batch_size=128,
                              shuffle=True,
                              num_workers=16,
                              collate_fn=pad)

train_iter_128 = data.DataLoader(dataset=train_dataset,
                              batch_size=128,
                              shuffle=True,
                              num_workers=16,
                              collate_fn=pad)

print(f'train_iter size: {len(train_iter)}')
print(f'eval_iter size: {len(eval_iter)}')
print(f'test_iter size: {len(test_iter)}')

77703
12267
2051


In [0]:
#experiment_code
# wget.download('https://archive.org/download/auto_manual_annots.tar/auto_manual_annots.tar.gz')

'auto_manual_annots.tar.gz'

In [0]:
#experiment_code
# import tarfile
# tar =  tarfile.open('./auto_manual_annots.tar.gz', mode='r')
# tar.extractall('./auto_manual_annots')
# tar.close()

In [0]:
#experiment_code
man_annot_paths = sorted([os.path.join(f[0], name) for f in os.walk('/content/auto_manual_annots') 
                if len(f[2])!=0 for name in f[2] if os.path.splitext(name)[-1] == '.txt' and name.split('_')[0]=='man'],
               key=lambda path: int(path.split('_')[-1].split('.')[0]))
aut_annot_paths = sorted([os.path.join(f[0], name) for f in os.walk('/content/auto_manual_annots') 
                if len(f[2])!=0 for name in f[2] if os.path.splitext(name)[-1] == '.txt' and name.split('_')[0]=='aut'],
               key=lambda path: int(path.split('_')[-1].split('.')[0]))

In [0]:
#experiment_code
man_test_dataset = NerDataset(man_annot_paths[0])
_ = [man_test_dataset.append(NerDataset(man_file)) for man_file in man_annot_paths[1:]]

aut_test_dataset = NerDataset(aut_annot_paths[0])
_ = [aut_test_dataset.append(NerDataset(aut_file)) for aut_file in aut_annot_paths[1:]]

man_test_iter = data.DataLoader(dataset=man_test_dataset,
                              batch_size=1,
                              shuffle=True,
                              num_workers=16,
                              collate_fn=pad)

aut_test_iter = data.DataLoader(dataset=aut_test_dataset,
                              batch_size=1,
                              shuffle=True,
                              num_workers=16,
                              collate_fn=pad)


print(f'man_test_iter iterator size: {len(man_test_iter)}')
print(f'aut_test_iter iterator size: {len(aut_test_iter)}')

320
426


In [0]:
#experiment_code
import zipfile
#run cell 1 first
wget.download('https://archive.org/download/manual_annotations/manual_annotations.zip')
tar = zipfile.ZipFile('/content/manual_annotations.zip', mode='r')
tar.extractall()
tar.close()

In [0]:
#experiment_code
import os
paths_man_annot = sorted([os.path.join(f[0], name) for f in os.walk('./manual_annotations') 
                if len(f[2])!=0 for name in f[2] if os.path.splitext(name)[-1] == '.txt' and name.split('_')[0]=='manual'],
               key=lambda path: int(path.split('_')[-1].split('.')[0]))

## tag counts

In [0]:
#experiment_code
dataiters = [train_iter, eval_iter, test_iter, man_test_iter]
tag_dict_list = []
for iterator in dataiters:
    tag_c_dict = {'B-BD':0, 'B-BP':0, 'B-PR':0, 'B-SP':0, 'B-CH':0, 'B-ED':0}  
    Words, Is_heads, Tags, Y, Y_hat = [], [], [], [], []  
    for i, batch in enumerate(iterator):
        words, x, is_heads, tags, y, seqlens = batch
        Words.extend(words)
        Tags.extend(tags)
        tags = tags[0].split()
        # found_tags = set(tag_c_dict.keys()) & set(tags) 
        for key in tag_c_dict.keys():
            for tag in tags:
                if tag == key:
                   tag_c_dict[key] = tag_c_dict[key] + 1 
        # for tg_key in found_tags:
        #     tag_c_dict[tg_key] = tag_c_dict[tg_key] + 1
    tag_dict_list.append(tag_c_dict) 
    print(tag_c_dict)

{'B-BD': 16883, 'B-BP': 0, 'B-PR': 6326, 'B-SP': 25163, 'B-CH': 10824, 'B-ED': 24365}
{'B-BD': 2512, 'B-BP': 0, 'B-PR': 1509, 'B-SP': 3844, 'B-CH': 1846, 'B-ED': 3831}
{'B-BD': 303, 'B-BP': 0, 'B-PR': 331, 'B-SP': 609, 'B-CH': 604, 'B-ED': 534}
{'B-BD': 76, 'B-BP': 42, 'B-PR': 50, 'B-SP': 80, 'B-CH': 62, 'B-ED': 99}


{'B-BD': 16883, 'B-BP': 0, 'B-PR': 6326, 'B-SP': 25163, 'B-CH': 10824, 'B-ED': 24365}\
{'B-BD': 2512, 'B-BP': 0, 'B-PR': 1509, 'B-SP': 3844, 'B-CH': 1846, 'B-ED': 3831}\
{'B-BD': 303, 'B-BP': 0, 'B-PR': 331, 'B-SP': 609, 'B-CH': 604, 'B-ED': 534}

In [0]:
#experiment_code
pd.DataFrame.from_dict(tag_dict_list)

B-BD  B-BP  B-PR   B-SP   B-CH   B-ED
0  16883     0  6326  25163  10824  24365
1   2512     0  1509   3844   1846   3831
2    303     0   331    609    604    534
3     76    42    50     80     62     99

In [0]:
#experiment_code
len(training_files), len(eval_files), len(test_files), len(man_annot_paths)

(20039, 2744, 307, 91)

## manual and automated test files





In [0]:
#experiment_code
lines = []
ss = '/'.join(test_files[0].split('/')[1:-1])
aut_entries_A = []
man_entries_A = []
for i, pth in enumerate(paths_man_annot):
    aut_path = './' + ss + '/' + paths_man_annot[i].split('/')[-1][7:]
    # print(aut_path)
    file1 = open(aut_path, "r")   
    aut_lines = file1.read().split('\n\n')
    # aut_lines = file1.read().splitlines() 
    file1.close()
    man_path = paths_man_annot[i]
    file1 = open(man_path, "r")
    # print(man_path)
    man_lines = file1.read().split('\n\n')
    # man_lines = file1.read().splitlines() 
    file1.close()
    aut_entries = []
    man_entries = []
    for l in aut_lines:
        lis = l.splitlines()
        aut_entries.extend(lis)
    
    for l in man_lines:
        lis = l.splitlines()
        man_entries.extend(lis)

    aut_entries_ = []
    man_entries_ = []
    i = 0;
    for i, tu in enumerate(man_entries):
        # print(tu)
        io = i
        # print(tu.split())
        while True:
            au = aut_entries[i].split()
            # print(au)
            if len(au)>1 and len(tu.split())>1 and tu.split()[0] == au[0]:
                aut_entries_.append(aut_entries[i])
                man_entries_.append(tu)
                i = i + 1
                break
            i = i + 1
            if i == len(aut_entries):
                # print(aut_entries[io:])
                # print(man_entries[io:])
                break
    aut_entries_A.extend(aut_entries_)
    man_entries_A.extend(man_entries_)

In [0]:
#experiment_code
print(man_entries_A)
print(len(man_entries_A))

['Mary O', 'Kerry O', 'Kennedy O', '( O', 'born O', 'September B-BD', '8 I-BD', ', I-BD', '1959 I-BD', ') O', 'is O', 'an O', 'American O', 'human O', 'rights O', 'activist O', ', O', 'writer O', ', O', 'and O', 'president O', 'of O', 'Robert O', 'F. O', 'Kennedy O', 'Human O', 'Rights O', '. O', 'She O', 'is O', 'the O', 'seventh O', 'child O', 'and O', 'third O', 'daughter O', 'of O', 'Robert B-PR', 'F. I-PR', 'Kennedy I-PR', 'and O', 'Ethel B-PR', 'Skakel I-PR', '. O', 'During O', 'her O', '15-year O', 'marriage O', 'to O', 'now O', '– O', 'New O', 'York O', 'Governor O', 'Andrew O', 'Cuomo O', ', O', 'she O', 'was O', 'known O', 'as O', 'Kerry O', 'Kennedy O', 'Cuomo O', 'from O', '1990 O', 'to O', '2005 O', '. O', 'She O', 'is O', 'the O', 'president O', 'of O', 'Robert O', 'F. O', 'Kennedy O', 'Human O', 'Rights O', '. O', 'President O', 'John O', 'F. O', 'Kennedy O', 'and O', 'Senator O', 'Ted O', 'Kennedy O', 'were O', 'her O', 'uncles O', ', O', 'and O', 'she O', 'is O', 'a O'

In [0]:
#experiment_code
print(aut_entries_A)
print(len(aut_entries_A))

['Mary O', 'Kerry O', 'Kennedy O', '( O', 'born O', 'September B-BD', '8 I-BD', ', I-BD', '1959 I-BD', ') O', 'is O', 'an O', 'American O', 'human O', 'rights O', 'activist O', ', O', 'writer O', ', O', 'and O', 'president O', 'of O', 'Robert O', 'F. O', 'Kennedy O', 'Human O', 'Rights O', '. O', 'She O', 'is O', 'the O', 'seventh O', 'child O', 'and O', 'third O', 'daughter O', 'of O', 'Robert B-PR', 'F. I-PR', 'Kennedy I-PR', 'and O', 'Ethel B-PR', 'Skakel I-PR', '. O', 'During O', 'her O', '15-year O', 'marriage O', 'to O', 'now O', '– B-SP', 'New I-SP', 'York I-SP', 'Governor I-SP', 'Andrew I-SP', 'Cuomo I-SP', ', O', 'she O', 'was O', 'known O', 'as O', 'Kerry O', 'Kennedy O', 'Cuomo O', 'from O', '1990 O', 'to O', '2005 O', '. O', 'She O', 'is O', 'the O', 'president O', 'of O', 'Robert B-PR', 'F. I-PR', 'Kennedy I-PR', 'Human O', 'Rights O', '. O', 'President O', 'John O', 'F. O', 'Kennedy O', 'and O', 'Senator O', 'Ted O', 'Kennedy O', 'were O', 'her O', 'uncles O', ', O', 'and

### comparison of manual and automated annotations

In [0]:
#experiment_code
with open('compare_man_aut.txt', 'w+') as fout:
    # fout.write('manual auto\n')
    for a, b in zip(man_entries_A, aut_entries_A):
        fout.write(f"{a} {b}\n")

In [0]:
#experiment_code
import numpy as np
import os
tags = ['BD', 'BP', 'PR', 'SP', 'CH', 'ED']
VOCAB_list = ['<PAD>', 'O',]
for tag in tags:
    VOCAB_list.append('I-'+tag)
    VOCAB_list.append('B-'+tag)
VOCAB = tuple(VOCAB_list)
tag2idx = {tag: idx for idx, tag in enumerate(VOCAB)}
idx2tag = {idx: tag for idx, tag in enumerate(VOCAB)}

y_true =  np.array([tag2idx[line.split()[1]] for line in open("compare_man_aut.txt", 'r').read().splitlines() if len(line) > 0]) #original tags
y_pred =  np.array([tag2idx[line.split()[3]] for line in open("compare_man_aut.txt", 'r').read().splitlines() if len(line) > 0]) #predicted tags

num_proposed = len(y_pred[y_pred>1])
num_correct = (np.logical_and(y_true==y_pred, y_true>1)).astype(np.int).sum()
num_gold = len(y_true[y_true>1])

print(f"num_proposed:{num_proposed}")
print(f"num_correct:{num_correct}")
print(f"num_gold:{num_gold}")

try:
    precision = num_correct / num_proposed
except ZeroDivisionError:
    precision = 1.0

try:
    recall = num_correct / num_gold
except ZeroDivisionError:
    recall = 1.0

try:
    f1 = 2*precision*recall / (precision + recall)
except ZeroDivisionError:
    if precision*recall==0:
        f1=1.0
    else:
        f1=0

with open('cmp_result.txt', 'w') as fout:
    # result = open("temp", "r").read()
    # fout.write(f"{result}\n")
    fout.write(f"precision={precision}\n")
    fout.write(f"recall={recall}\n")
    fout.write(f"f1={f1}\n")

# os.remove("temp")
print("precision=%.2f"%precision)
print("recall=%.2f"%recall)
print("f1=%.2f"%f1) 

num_proposed:1433
num_correct:625
num_gold:1196
precision=0.44
recall=0.52
f1=0.48


|          |      |
|-------------|--------|
|num_proposed:|   1433 |
|num_correct:|625|
num_gold:|1196|
precision:|0.44
recall:|0.52
f1:|0.48

In [0]:
!pip install wget
import wget
wget.download('https://raw.githubusercontent.com/davidsbatista/NER-Evaluation/master/ner_evaluation/ner_eval.py')
from ner_eval import collect_named_entities
from ner_eval import compute_metrics
from ner_eval import compute_precision_recall_wrapper
from ner_eval import Entity
from ner_eval import Evaluator

In [0]:
#experiment_code
entries = open('compare_man_aut.txt', 'r').read().strip().split("\n\n")
sents, tags_li = [], [] # list of lists
ne_man = []
ne_aut = []
true = []
pred = []
for entry in entries:
    lines = entry.splitlines()
    words = [line.split()[0] for line in entry.splitlines() if len(line.split()) > 1]
    pred_tags = ([line.split()[-1] if line.split()[-1][2:]!='BP' else 'O' for line in entry.splitlines() if len(line.split()) > 1])
    man_tags  = ([line.split()[1] if line.split()[1][2:]!='BP' else 'O' for line in entry.splitlines() if len(line.split()) > 1])
    # man_tags = ([line.split()[1] if line.split()[1][2:]!='BP' for line in entry.splitlines() if len(line.split()) > 1])
    # man_tags = ([line.split()[1] for line in entry.splitlines() if len(line.split()) > 1])
    ne = collect_named_entities(man_tags)
    ne_man.extend(ne)
    true.append(man_tags)
    pred.append(pred_tags)
    ne = collect_named_entities(pred_tags)
    ne_aut.extend(ne)

In [0]:
from copy import deepcopy
from collections import defaultdict
def metric_calc(true, pred):
    metrics_results = {'correct': 0, 'incorrect': 0, 'partial': 0,
                    'missed': 0, 'spurious': 0, 'possible': 0, 'actual': 0, 'precision': 0, 'recall': 0}

    # overall results
    results = {'strict': deepcopy(metrics_results),
            'ent_type': deepcopy(metrics_results),
            'partial':deepcopy(metrics_results),
            'exact':deepcopy(metrics_results)
            }

    tags = ['BD', 'PR', 'SP', 'CH', 'ED']
    # results aggregated by entity type
    evaluation_agg_entities_type = {e: deepcopy(results) for e in tags}

    for true_ents, pred_ents in zip(true, pred):
        
        # compute results for one message
        tmp_results, tmp_agg_results = compute_metrics(
            collect_named_entities(true_ents), collect_named_entities(pred_ents),  tags
        )
        
        #print(tmp_results)

        # aggregate overall results
        for eval_schema in results.keys():
            for metric in metrics_results.keys():
                results[eval_schema][metric] += tmp_results[eval_schema][metric]
                
        # Calculate global precision and recall
            
        results = compute_precision_recall_wrapper(results)


        # aggregate results by entity type
    
        for e_type in tags:

            for eval_schema in tmp_agg_results[e_type]:

                for metric in tmp_agg_results[e_type][eval_schema]:
                    
                    evaluation_agg_entities_type[e_type][eval_schema][metric] += tmp_agg_results[e_type][eval_schema][metric]
                    
            # Calculate precision recall at the individual entity level
                    
            evaluation_agg_entities_type[e_type] = compute_precision_recall_wrapper(evaluation_agg_entities_type[e_type])
    for k, dic in results.items():
        f1 = 2*results[k]['precision']*results[k]['recall'] / (results[k]['precision'] + results[k]['recall'])
        results[k]['f1'] = f1
    return results

In [0]:
#experiment_code
results = metric_calc(true, pred)
results

{'ent_type': {'actual': 528,
  'correct': 243,
  'f1': 0.5418060200668897,
  'incorrect': 6,
  'missed': 120,
  'partial': 0,
  'possible': 369,
  'precision': 0.4602272727272727,
  'recall': 0.6585365853658537,
  'spurious': 279},
 'exact': {'actual': 528,
  'correct': 169,
  'f1': 0.37681159420289856,
  'incorrect': 80,
  'missed': 120,
  'partial': 0,
  'possible': 369,
  'precision': 0.32007575757575757,
  'recall': 0.45799457994579945,
  'spurious': 279},
 'partial': {'actual': 528,
  'correct': 169,
  'f1': 0.4659977703455964,
  'incorrect': 0,
  'missed': 120,
  'partial': 80,
  'possible': 369,
  'precision': 0.3958333333333333,
  'recall': 0.5663956639566395,
  'spurious': 279},
 'strict': {'actual': 528,
  'correct': 166,
  'f1': 0.37012263099219617,
  'incorrect': 83,
  'missed': 120,
  'partial': 0,
  'possible': 369,
  'precision': 0.3143939393939394,
  'recall': 0.44986449864498645,
  'spurious': 279}}

In [0]:
#experiment_code
import pandas as pd
pd.DataFrame.from_dict(results)

ent_type     partial      strict       exact
correct    243.000000  169.000000  166.000000  169.000000
incorrect    6.000000    0.000000   83.000000   80.000000
partial      0.000000   80.000000    0.000000    0.000000
missed     120.000000  120.000000  120.000000  120.000000
spurious   279.000000  279.000000  279.000000  279.000000
possible   369.000000  369.000000  369.000000  369.000000
actual     528.000000  528.000000  528.000000  528.000000
precision    0.460227    0.395833    0.314394    0.320076
recall       0.658537    0.566396    0.449864    0.457995
f1           0.541806    0.465998    0.370123    0.376812

## Creating the new test set

In [0]:
#experiment_code
lines = []
ss = '/'.join(test_files[0].split('/')[1:-1])
aut_entries_A = []
man_entries_A = []
line_counts = []
for i, pth in enumerate(paths_man_annot):
    aut_path = './' + ss + '/' + paths_man_annot[i].split('/')[-1][7:]
    # print(aut_path)
    file1 = open(aut_path, "r")   
    aut_lines = file1.read().split('\n\n')
    # aut_lines = file1.read().splitlines() 
    file1.close()
    man_path = paths_man_annot[i]
    file1 = open(man_path, "r")
    # print(man_path)
    man_lines = file1.read().split('\n\n')
    
    # man_lines = file1.read().splitlines() 
    file1.close()
    aut_entries = []
    man_entries = []
    au_l_c = []
    ma_l_c = []
    for l in aut_lines:
        lis = l.splitlines()
        au_l_c.append(len(lis))
        aut_entries.extend(lis)
    
    for l in man_lines:
        lis = l.splitlines()
        ma_l_c.append(len(lis))
        man_entries.extend(lis)
    
    # assert ma_l_c == au_l_c
    
    line_counts.append(ma_l_c)

    aut_entries_ = []
    man_entries_ = []
    i = 0;
    for i, tu in enumerate(man_entries):
        # print(tu)
        # io = i
        # print(tu.split())
        while True:
            au = aut_entries[i].split()
            # print(au)
            if len(au)>1 and len(tu.split())>1 and tu.split()[0] == au[0]:
                aut_entries_.append(aut_entries[i])
                man_entries_.append(tu)
                i = i + 1
                break
            i = i + 1
            if i == len(aut_entries):
                # print(aut_entries[io:])
                # print(man_entries[io:])
                break
    assert len(aut_entries_) == len(man_entries_)
    aut_entries_A.append(aut_entries_)
    man_entries_A.append(man_entries_)

In [0]:
#experiment_code
print(man_entries_A)
print(len(man_entries_A))

[['Mary O', 'Kerry O', 'Kennedy O', '( O', 'born O', 'September B-BD', '8 I-BD', ', I-BD', '1959 I-BD', ') O', 'is O', 'an O', 'American O', 'human O', 'rights O', 'activist O', ', O', 'writer O', ', O', 'and O', 'president O', 'of O', 'Robert O', 'F. O', 'Kennedy O', 'Human O', 'Rights O', '. O', 'She O', 'is O', 'the O', 'seventh O', 'child O', 'and O', 'third O', 'daughter O', 'of O', 'Robert B-PR', 'F. I-PR', 'Kennedy I-PR', 'and O', 'Ethel B-PR', 'Skakel I-PR', '. O', 'During O', 'her O', '15-year O', 'marriage O', 'to O', 'now O', '– O', 'New O', 'York O', 'Governor O', 'Andrew O', 'Cuomo O', ', O', 'she O', 'was O', 'known O', 'as O', 'Kerry O', 'Kennedy O', 'Cuomo O', 'from O', '1990 O', 'to O', '2005 O', '. O', 'She O', 'is O', 'the O', 'president O', 'of O', 'Robert O', 'F. O', 'Kennedy O', 'Human O', 'Rights O', '. O', 'President O', 'John O', 'F. O', 'Kennedy O', 'and O', 'Senator O', 'Ted O', 'Kennedy O', 'were O', 'her O', 'uncles O', ', O', 'and O', 'she O', 'is O', 'a O

In [0]:
#experiment_code
print(aut_entries_A)
print(len(aut_entries_A))

[['Mary O', 'Kerry O', 'Kennedy O', '( O', 'born O', 'September B-BD', '8 I-BD', ', I-BD', '1959 I-BD', ') O', 'is O', 'an O', 'American O', 'human O', 'rights O', 'activist O', ', O', 'writer O', ', O', 'and O', 'president O', 'of O', 'Robert O', 'F. O', 'Kennedy O', 'Human O', 'Rights O', '. O', 'She O', 'is O', 'the O', 'seventh O', 'child O', 'and O', 'third O', 'daughter O', 'of O', 'Robert B-PR', 'F. I-PR', 'Kennedy I-PR', 'and O', 'Ethel B-PR', 'Skakel I-PR', '. O', 'During O', 'her O', '15-year O', 'marriage O', 'to O', 'now O', '– B-SP', 'New I-SP', 'York I-SP', 'Governor I-SP', 'Andrew I-SP', 'Cuomo I-SP', ', O', 'she O', 'was O', 'known O', 'as O', 'Kerry O', 'Kennedy O', 'Cuomo O', 'from O', '1990 O', 'to O', '2005 O', '. O', 'She O', 'is O', 'the O', 'president O', 'of O', 'Robert B-PR', 'F. I-PR', 'Kennedy I-PR', 'Human O', 'Rights O', '. O', 'President O', 'John O', 'F. O', 'Kennedy O', 'and O', 'Senator O', 'Ted O', 'Kennedy O', 'were O', 'her O', 'uncles O', ', O', 'an

In [0]:
#experiment_code
len(line_counts)

91

In [0]:
#experiment_code
print(line_counts[0])

[28, 16, 25, 11, 44, 12, 8, 26, 14, 33, 7, 22, 33, 21, 36, 21, 33, 18, 24, 48, 1, 6, 30, 5, 1, 5, 6, 7, 5, 2, 5, 1, 14, 7, 3, 6, 6, 4, 2, 5, 6, 9, 19, 2, 11, 5, 5, 1, 3, 2, 6, 10, 2, 12, 2, 10, 13, 3, 2, 26, 6, 11, 15, 40, 38, 40, 25, 29, 11, 33, 44, 26, 15, 25, 13, 44, 18, 25, 13, 32, 24, 49, 19, 73, 23, 10, 11, 28, 14, 29, 38, 38, 35, 22, 14, 50, 35, 20, 30, 39, 29, 32, 61, 81, 19, 8, 53, 47, 19, 24, 41, 22, 17, 45, 22, 35, 27, 14, 33, 50, 21, 34, 28, 20, 68, 34, 1, 26, 29, 58, 21, 37, 3, 34, 40, 1, 36, 15, 24, 24, 10, 7, 17, 17, 28, 31, 9, 14, 70, 28, 1, 33, 22, 13, 13, 1, 34, 1, 13, 19, 13, 18, 1, 15, 27, 31, 26, 12, 1, 20, 1, 9, 11, 6, 1, 5, 1, 25, 46, 1, 0]


In [0]:
#experiment_code
for a, m in zip(aut_entries_A, man_entries_A):
    # for y, x in zip(a,m):
        # assert len(y.split()) == len(x.split()), f'{len(y)} != {len(x)} {x}, {y}'
    assert len(a) == len(m), f'{len(y)} != {len(x)}'

In [0]:
#experiment_code
os.mkdir('./auto_manual_annots')

In [0]:
#experiment_code
for i, (counts, aut, man) in enumerate(zip(line_counts, aut_entries_A, man_entries_A)):
    with open(f'./auto_manual_annots/aut_{i}.txt', 'w+')as auf, open(f'./auto_manual_annots/man_{i}.txt', 'w+')as maf:
        start = 0; 
        for count in counts:
            au_line = aut[start:start+count]
            ma_line = man[start:start+count]
            start = start + count 
            for a_tag, m_tag in zip(au_line, ma_line):
                auf.write(f'{a_tag}\n')
                maf.write(f'{m_tag}\n')
            auf.write('\n')
            maf.write('\n')

In [0]:
#experiment_code
import tarfile
tar =  tarfile.open('auto_manual_annots.tar.gz', mode='w:gz')
tar.add('./auto_manual_annots')
tar.close()

## BERT NER performance on Manual annotations

In [0]:
#experiment_code
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/drive


In [0]:
#experiment_code
# fname = '/content/drive/My Drive/imrsv/Colab Notebooks/weights_overall.pt'
fname = '/content/drive/My Drive/imrsv/weights_overall_P0.79_R0.70_F0.74.pt'

finetuning = True
top_rnns = False
device = 'cuda' if torch.cuda.is_available() else 'cpu'
model = Net(top_rnns=top_rnns, vocab_size=len(VOCAB), device=device, finetuning=finetuning).cuda()
model = nn.DataParallel(model)
model.load_state_dict(torch.load(fname))

100%|██████████| 404400730/404400730 [00:09<00:00, 40865350.70B/s]


<All keys matched successfully>

In [0]:
#experiment_code
man_test_dataset = NerDataset(paths_man_annot[0])
_ = [man_test_dataset.append(NerDataset(man_file)) for man_file in paths_man_annot[1:]]

man_test_iter = data.DataLoader(dataset=man_test_dataset,
                              batch_size=1,
                              shuffle=True,
                              num_workers=16,
                              collate_fn=pad)
print(len(man_test_iter))

320


In [0]:
#experiment_code
precision, recall, f1 = eval(model, man_test_iter, './eval')

num_proposed:992
num_correct:727
num_gold:1180
precision=0.73
recall=0.62
f1=0.67


|          |      |
|-------------|--------|
|num_proposed:|   992 |
|num_correct:|727|
num_gold:|1180|
precision:|0.73
recall:|0.62
f1:|0.67

In [0]:
#experiment_code
wget.download('https://archive.org/download/auto_manual_annots.tar/auto_manual_annots.tar.gz')

'auto_manual_annots.tar (1).gz'

In [0]:
#experiment_code
import tarfile
tar =  tarfile.open('/content/auto_manual_annots.tar.gz', mode='r')
tar.extractall()
tar.close()

In [0]:
#experiment_code
man_annot_paths = sorted([os.path.join(f[0], name) for f in os.walk('./auto_manual_annots') 
                if len(f[2])!=0 for name in f[2] if os.path.splitext(name)[-1] == '.txt' and name.split('_')[0]=='man'],
               key=lambda path: int(path.split('_')[-1].split('.')[0]))
aut_annot_paths = sorted([os.path.join(f[0], name) for f in os.walk('./auto_manual_annots') 
                if len(f[2])!=0 for name in f[2] if os.path.splitext(name)[-1] == '.txt' and name.split('_')[0]=='aut'],
               key=lambda path: int(path.split('_')[-1].split('.')[0]))

In [0]:
#experiment_code
len(aut_annot_paths)
# aut_annot_paths

91

In [0]:
#experiment_code
len(man_annot_paths)
# man_annot_paths

91

In [0]:
#experiment_code
man_test_dataset = NerDataset(man_annot_paths[0])
_ = [man_test_dataset.append(NerDataset(man_file)) for man_file in man_annot_paths[1:]]

aut_test_dataset = NerDataset(aut_annot_paths[0])
_ = [aut_test_dataset.append(NerDataset(aut_file)) for aut_file in aut_annot_paths[1:]]

man_test_iter = data.DataLoader(dataset=man_test_dataset,
                              batch_size=1,
                              shuffle=True,
                              num_workers=16,
                              collate_fn=pad)

aut_test_iter = data.DataLoader(dataset=aut_test_dataset,
                              batch_size=1,
                              shuffle=True,
                              num_workers=16,
                              collate_fn=pad)


print(len(man_test_iter))
print(len(aut_test_iter))

320
426


In [0]:
#experiment_code
len(man_test_dataset)

320

In [0]:
#experiment_code
len(aut_test_dataset)

426

In [0]:
#experiment_code
aligned_indices = []
for i, (aut_path, man_path) in enumerate(zip(aut_annot_paths, man_annot_paths)):
    # assert len(NerDataset(aut_path)) == len(NerDataset(man_path)), f'in file {i}: {len(NerDataset(aut_path))} != {len(NerDataset(man_path))}'
    if len(NerDataset(aut_path)) == len(NerDataset(man_path)):
        aligned_indices.append(i)

In [0]:
#experiment_code
len(aligned_indices)

28

In [0]:
#experiment_code
man_annot_paths_ = [man_annot_paths[idx] for idx in  aligned_indices]
aut_annot_paths_ = [aut_annot_paths[idx] for idx in  aligned_indices]

In [0]:
#experiment_code
man_test_dataset = NerDataset(man_annot_paths_[0])
_ = [man_test_dataset.append(NerDataset(man_file)) for man_file in man_annot_paths_[1:]]

aut_test_dataset = NerDataset(aut_annot_paths_[0])
_ = [aut_test_dataset.append(NerDataset(aut_file)) for aut_file in aut_annot_paths_[1:]]

man_test_iter = data.DataLoader(dataset=man_test_dataset,
                              batch_size=1,
                              shuffle=True,
                              num_workers=16,
                              collate_fn=pad)

aut_test_iter = data.DataLoader(dataset=aut_test_dataset,
                              batch_size=1,
                              shuffle=True,
                              num_workers=16,
                              collate_fn=pad)


print(len(man_test_iter))
print(len(aut_test_iter))

72
72


In [0]:
#experiment_code
entries = open('/content/eval.P0.73_R0.62_F0.67', 'r').read().strip().split("\n\n")
sents, tags_li = [], [] # list of lists
for entry in entries:
    lines = entry.splitlines()
    words = [line.split()[0] for line in entry.splitlines() if len(line.split()) > 1]
    pred_tags = ([line.split()[-1] for line in entry.splitlines() if len(line.split()) > 1])
    man_tags = ([line.split()[1] for line in entry.splitlines() if len(line.split()) > 1])

In [0]:
#experiment_code
# remember to exclude the BP
from ner_evaluation.ner_eval import Evaluator


In [0]:
#experiment_code
!pip install wget
import wget
wget.download('https://raw.githubusercontent.com/davidsbatista/NER-Evaluation/master/ner_evaluation/ner_eval.py')
from ner_eval import collect_named_entities
from ner_eval import compute_metrics
from ner_eval import compute_precision_recall_wrapper
from ner_eval import Entity
from ner_eval import Evaluator

  Created wheel for wget: filename=wget-3.2-cp36-none-any.whl size=9682 sha256=b51b1b7532bdce7019ada5649fbc3c16a91e5450e64d56df31cbe8cae0eaab74
  Stored in directory: /root/.cache/pip/wheels/40/15/30/7d8f7cea2902b4db79e3fea550d7d7b85ecb27ef992b618f3f
Successfully built wget


In [0]:
#experiment_code
true = [Entity(e_type='MISC', start_offset=12, end_offset=12),
        Entity(e_type='LOC', start_offset=15, end_offset=15),
        Entity(e_type='PER', start_offset=37, end_offset=39),
        Entity(e_type='ORG', start_offset=45, end_offset=46)]
pred = [Entity(e_type='MISC', start_offset=12, end_offset=12),
        Entity(e_type='LOC', start_offset=10, end_offset=11),
        Entity(e_type='PER', start_offset=37, end_offset=39),
        Entity(e_type='LOC', start_offset=45, end_offset=46)]
compute_metrics(true, pred, ['LOC', 'MISC', 'PER', 'ORG'])
# evaluator = Evaluator(true, pred, ['LOC', 'MISC', 'PER', 'ORG'])
# results, results_agg = evaluator.evaluate()

In [0]:
#experiment_code
entries = open('/content/eval.P0.73_R0.62_F0.67', 'r').read().strip().split("\n\n")
sents, tags_li = [], [] # list of lists
ne_man = []
ne_aut = []
true = []
pred = []
for entry in entries:
    lines = entry.splitlines()
    words = [line.split()[0] for line in entry.splitlines() if len(line.split()) > 1]
    pred_tags = ([line.split()[-1] if line.split()[-1][2:]!='BP' else 'O' for line in entry.splitlines() if len(line.split()) > 1])
    man_tags  = ([line.split()[1] if line.split()[1][2:]!='BP' else 'O' for line in entry.splitlines() if len(line.split()) > 1])
    # man_tags = ([line.split()[1] if line.split()[1][2:]!='BP' for line in entry.splitlines() if len(line.split()) > 1])
    # man_tags = ([line.split()[1] for line in entry.splitlines() if len(line.split()) > 1])
    ne = collect_named_entities(man_tags)
    ne_man.extend(ne)
    true.append(man_tags)
    pred.append(pred_tags)
    ne = collect_named_entities(pred_tags)
    ne_aut.extend(ne)

In [0]:
#experiment_code
# f = lambda i: i%2==0 ? i: 0
[i if i%2==0 else 0 for i in [1,2,3,4,5,6,7,8,9,10]]

[0, 2, 0, 4, 0, 6, 0, 8, 0, 10]

In [0]:
#experiment_code
from copy import deepcopy
from collections import defaultdict
metrics_results = {'correct': 0, 'incorrect': 0, 'partial': 0,
                   'missed': 0, 'spurious': 0, 'possible': 0, 'actual': 0, 'precision': 0, 'recall': 0}

# overall results
results = {'strict': deepcopy(metrics_results),
           'ent_type': deepcopy(metrics_results),
           'partial':deepcopy(metrics_results),
           'exact':deepcopy(metrics_results)
          }

tags = ['BD', 'PR', 'SP', 'CH', 'ED']
# results aggregated by entity type
evaluation_agg_entities_type = {e: deepcopy(results) for e in tags}

for true_ents, pred_ents in zip(true, pred):
    
    # compute results for one message
    tmp_results, tmp_agg_results = compute_metrics(
        collect_named_entities(true_ents), collect_named_entities(pred_ents),  tags
    )
    
    #print(tmp_results)

    # aggregate overall results
    for eval_schema in results.keys():
        for metric in metrics_results.keys():
            results[eval_schema][metric] += tmp_results[eval_schema][metric]
            
    # Calculate global precision and recall
        
    results = compute_precision_recall_wrapper(results)


    # aggregate results by entity type
 
    for e_type in tags:

        for eval_schema in tmp_agg_results[e_type]:

            for metric in tmp_agg_results[e_type][eval_schema]:
                
                evaluation_agg_entities_type[e_type][eval_schema][metric] += tmp_agg_results[e_type][eval_schema][metric]
                
        # Calculate precision recall at the individual entity level
                
        evaluation_agg_entities_type[e_type] = compute_precision_recall_wrapper(evaluation_agg_entities_type[e_type])

In [0]:
#experiment_code
results

{'ent_type': {'actual': 339,
  'correct': 280,
  'incorrect': 2,
  'missed': 83,
  'partial': 0,
  'possible': 365,
  'precision': 0.8259587020648967,
  'recall': 0.7671232876712328,
  'spurious': 57},
 'exact': {'actual': 339,
  'correct': 195,
  'incorrect': 87,
  'missed': 83,
  'partial': 0,
  'possible': 365,
  'precision': 0.5752212389380531,
  'recall': 0.5342465753424658,
  'spurious': 57},
 'partial': {'actual': 339,
  'correct': 195,
  'incorrect': 0,
  'missed': 83,
  'partial': 87,
  'possible': 365,
  'precision': 0.7035398230088495,
  'recall': 0.6534246575342466,
  'spurious': 57},
 'strict': {'actual': 339,
  'correct': 193,
  'incorrect': 89,
  'missed': 83,
  'partial': 0,
  'possible': 365,
  'precision': 0.5693215339233039,
  'recall': 0.5287671232876713,
  'spurious': 57}}

In [0]:
#experiment_code
for k, dic in results.items():
    f1 = 2*results[k]['precision']*results[k]['recall'] / (results[k]['precision'] + results[k]['recall'])
    results[k]['f1'] = f1

In [0]:
#experiment_code
results

{'ent_type': {'actual': 339,
  'correct': 280,
  'f1': 0.7954545454545453,
  'incorrect': 2,
  'missed': 83,
  'partial': 0,
  'possible': 365,
  'precision': 0.8259587020648967,
  'recall': 0.7671232876712328,
  'spurious': 57},
 'exact': {'actual': 339,
  'correct': 195,
  'f1': 0.5539772727272727,
  'incorrect': 87,
  'missed': 83,
  'partial': 0,
  'possible': 365,
  'precision': 0.5752212389380531,
  'recall': 0.5342465753424658,
  'spurious': 57},
 'partial': {'actual': 339,
  'correct': 195,
  'f1': 0.6775568181818182,
  'incorrect': 0,
  'missed': 83,
  'partial': 87,
  'possible': 365,
  'precision': 0.7035398230088495,
  'recall': 0.6534246575342466,
  'spurious': 57},
 'strict': {'actual': 339,
  'correct': 193,
  'f1': 0.5482954545454546,
  'incorrect': 89,
  'missed': 83,
  'partial': 0,
  'possible': 365,
  'precision': 0.5693215339233039,
  'recall': 0.5287671232876713,
  'spurious': 57}}

In [0]:
#experiment_code
import pandas as pd
pd.DataFrame.from_dict(results)

ent_type     partial      strict       exact
correct    280.000000  195.000000  193.000000  195.000000
incorrect    2.000000    0.000000   89.000000   87.000000
partial      0.000000   87.000000    0.000000    0.000000
missed      83.000000   83.000000   83.000000   83.000000
spurious    57.000000   57.000000   57.000000   57.000000
possible   365.000000  365.000000  365.000000  365.000000
actual     339.000000  339.000000  339.000000  339.000000
precision    0.825959    0.703540    0.569322    0.575221
recall       0.767123    0.653425    0.528767    0.534247
f1           0.795455    0.677557    0.548295    0.553977


|   |type |	partial  |	strict  | exact  |
|---|------|----------|----------|--------|
|correct|	280.000000|	195.000000|	193.000000|	195.000000|
|incorrect|	2.000000|	0.000000|	89.000000|	87.000000|
|partial|	0.000000|	87.000000|	0.000000|	0.000000|
|missed	|83.000000	|83.000000	|83.000000	|83.000000|
|spurious	|57.000000	|57.000000	|57.000000|	57.000000|
|possible|	365.000000|	365.000000|	365.000000|	365.000000|
|actual	|339.000000	|339.000000	|339.000000|	339.000000|
|precision|	0.825959|	0.703540|	0.569322|	0.575221|
|recall	|0.767123|	0.653425|	0.528767|	0.534247|
|f1|	0.795455|	0.677557|	0.548295|	0.553977|